Lambda School Data Science

*Unit 2, Sprint 3, Module 1*

---


# Define ML problems

You will use your portfolio project dataset for all assignments this sprint.

## Assignment

Complete these tasks for your project, and document your decisions.

- [ ] Choose your target. Which column in your tabular dataset will you predict?
- [ ] Is your problem regression or classification?
- [ ] How is your target distributed?
    - Classification: How many classes? Are the classes imbalanced?
    - Regression: Is the target right-skewed? If so, you may want to log transform the target.
- [ ] Choose your evaluation metric(s).
    - Classification: Is your majority class frequency >= 50% and < 70% ? If so, you can just use accuracy if you want. Outside that range, accuracy could be misleading. What evaluation metric will you choose, in addition to or instead of accuracy?
    - Regression: Will you use mean absolute error, root mean squared error, R^2, or other regression metrics?
- [ ] Choose which observations you will use to train, validate, and test your model.
    - Are some observations outliers? Will you exclude them?
    - Will you do a random split or a time-based split?
- [ ] Begin to clean and explore your data.
- [ ] Begin to choose which features, if any, to exclude. Would some features "leak" future information?

If you haven't found a dataset yet, do that today. [Review requirements for your portfolio project](https://lambdaschool.github.io/ds/unit2) and choose your dataset.

Some students worry, ***what if my model isn't “good”?*** Then, [produce a detailed tribute to your wrongness. That is science!](https://twitter.com/nathanwpyle/status/1176860147223867393)

# My Portfolio Dataset

In [14]:
import warnings
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OrdinalEncoder
from sklearn.impute import SimpleImputer
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.pipeline import make_pipeline
from sklearn.metrics import r2_score, mean_squared_error

warnings.filterwarnings('ignore')

## Exploratory Data Analysis

In [15]:
data_url = './data/ab_us_2020.csv'
df = pd.read_csv(data_url)

print(df.shape)
df.head()

(226030, 17)


id                                               name  host_id  \
0   38585    Charming Victorian home - twin beds + breakfast   165529   
1   80905                                   French Chic Loft   427027   
2  108061  Walk to stores/parks/downtown. Fenced yard/Pet...   320564   
3  155305                 Cottage! BonPaul + Sharky's Hostel   746673   
4  160594                                Historic Grove Park   769252   

   host_name neighbourhood_group neighbourhood  latitude  longitude  \
0    Evelyne                 NaN         28804  35.65146  -82.62792   
1    Celeste                 NaN         28801  35.59779  -82.55540   
2       Lisa                 NaN         28801  35.60670  -82.55563   
3    BonPaul                 NaN         28806  35.57864  -82.59578   
4  Elizabeth                 NaN         28801  35.61442  -82.54127   

         room_type  price  minimum_nights  number_of_reviews last_review  \
0     Private room     60               1                138    16/02/20   
1  Entire home/apt    470               1                114    07/09/20   
2  Entire home/apt     75              30                 89    30/11/19   
3  Entire home/apt     90               1                267    22/09/20   
4     Private room    125              30                 58    19/10/15   

   reviews_per_month  calculated_host_listings_count  availability_365  \
0               1.14                               1                 0   
1               1.03                              11               288   
2               0.81                               2               298   
3               2.39                               5                 0   
4               0.52                               1                 0   

        city  
0  Asheville  
1  Asheville  
2  Asheville  
3  Asheville  
4  Asheville

In [3]:
ProfileReport(df)

---

## Data Cleaning

In [4]:
df.describe(include='number')

id       host_id       latitude      longitude  \
count  2.260300e+05  2.260300e+05  226030.000000  226030.000000   
mean   2.547176e+07  9.352385e+07      35.662829    -103.220662   
std    1.317814e+07  9.827422e+07       6.849855      26.222091   
min    1.090000e+02  2.300000e+01      18.920990    -159.714900   
25%    1.515890e+07  1.399275e+07      32.761783    -118.598115   
50%    2.590916e+07  5.138266e+07      37.261125     -97.817200   
75%    3.772624e+07  1.497179e+08      40.724038     -76.919322   
max    4.556085e+07  3.679176e+08      47.734620     -70.995950   

               price  minimum_nights  number_of_reviews  reviews_per_month  \
count  226030.000000    2.260300e+05      226030.000000       177428.00000   
mean      219.716529    4.525490e+02          34.506530            1.43145   
std       570.353609    2.103376e+05          63.602914            1.68321   
min         0.000000    1.000000e+00           0.000000            0.01000   
25%        75.000000    1.000000e+00           1.000000            0.23000   
50%       121.000000    2.000000e+00           8.000000            0.81000   
75%       201.000000    7.000000e+00          39.000000            2.06000   
max     24999.000000    1.000000e+08         966.000000           44.06000   

       calculated_host_listings_count  availability_365  
count                   226030.000000     226030.000000  
mean                        16.698562        159.314856  
std                         51.068966        140.179628  
min                          1.000000          0.000000  
25%                          1.000000          0.000000  
50%                          2.000000        140.000000  
75%                          6.000000        311.000000  
max                        593.000000        365.000000

In [5]:
# Find the count of outliers
mask = df['minimum_nights'] >= 500
df[mask]['minimum_nights'].value_counts()

1000         18
500          13
1125          6
1124          3
700           2
999           2
600           2
950           1
750           1
1123          1
1250          1
800           1
730           1
100000000     1
Name: minimum_nights, dtype: int64

In [6]:
print(df['minimum_nights'].max())

100000000


In [7]:
outlier_index = df['minimum_nights'].argmax()
df = df.drop(outlier_index)
df.describe(include='number')

id       host_id       latitude      longitude  \
count  2.260290e+05  2.260290e+05  226029.000000  226029.000000   
mean   2.547180e+07  9.352426e+07      35.662820    -103.220577   
std    1.317815e+07  9.827424e+07       6.849869      26.222118   
min    1.090000e+02  2.300000e+01      18.920990    -159.714900   
25%    1.515888e+07  1.399275e+07      32.761780    -118.598010   
50%    2.590916e+07  5.138445e+07      37.261100     -97.817150   
75%    3.772633e+07  1.497188e+08      40.724040     -76.919210   
max    4.556085e+07  3.679176e+08      47.734620     -70.995950   

               price  minimum_nights  number_of_reviews  reviews_per_month  \
count  226029.000000   226029.000000      226029.000000      177427.000000   
mean      219.717200       10.129873          34.506647           1.431458   
std       570.354782       25.251182          63.603030           1.683212   
min         0.000000        1.000000           0.000000           0.010000   
25%        75.000000        1.000000           1.000000           0.230000   
50%       121.000000        2.000000           8.000000           0.810000   
75%       201.000000        7.000000          39.000000           2.060000   
max     24999.000000     1250.000000         966.000000          44.060000   

       calculated_host_listings_count  availability_365  
count                   226029.000000     226029.000000  
mean                        16.698632        159.315561  
std                         51.069068        140.179538  
min                          1.000000          0.000000  
25%                          1.000000          0.000000  
50%                          2.000000        140.000000  
75%                          6.000000        311.000000  
max                        593.000000        365.000000

In [8]:
# Drop irrelevant features
df = df.copy().drop(
  columns=['name', 'host_id', 'host_name', 'neighbourhood_group', 'reviews_per_month']
)
df.set_index('id', inplace=True)

print(df.shape)

(226029, 11)


---
## Feature and Target Selection


In [12]:
# Feature and target matrices
target = 'price'
X = df.drop(target, axis=1)
y = df[target]

print(f"Features: {len(X.columns)}")
X.head()

Features: 10


neighbourhood  latitude  longitude        room_type  minimum_nights  \
id                                                                           
38585          28804  35.65146  -82.62792     Private room               1   
80905          28801  35.59779  -82.55540  Entire home/apt               1   
108061         28801  35.60670  -82.55563  Entire home/apt              30   
155305         28806  35.57864  -82.59578  Entire home/apt               1   
160594         28801  35.61442  -82.54127     Private room              30   

        number_of_reviews last_review  calculated_host_listings_count  \
id                                                                      
38585                 138    16/02/20                               1   
80905                 114    07/09/20                              11   
108061                 89    30/11/19                               2   
155305                267    22/09/20                               5   
160594                 58    19/10/15                               1   

        availability_365       city  
id                                   
38585                  0  Asheville  
80905                288  Asheville  
108061               298  Asheville  
155305                 0  Asheville  
160594                 0  Asheville

---



### ML Problems

Target: price

Predicting the price of an Airbnb unit is a regression problem. To model this problem, I'll build a pipeline using both linear and random forest regression algorithms.


Metrics: r^2 score, mean-squared-error (MSE

---
## Training, Validation, and Testing Datasets

In [11]:
# Split into training, validation, and testing subsets
X_train, X_test, y_train, y_test = train_test_split(
  X, y, test_size=0.2, random_state=122995
)

X_train, X_val, y_train, y_val = train_test_split(
  X_train, y_train, test_size=0.2, random_state=122995
)

print(f"""
  Training dataset: {len(X_train) / len(df) *100}%
  Validation dataset: {len(X_val) / len(df) *100}%
  Testing dataset: {len(X_test) / len(df) *100}%
""")


  Training dataset: 63.99975224418105%
  Validation dataset: 16.00015927159789%
  Testing dataset: 20.000088484221052%

